In [1]:
import torch
import torch.nn as nn
import torch.optim as optim
import torchvision.transforms as transforms
from torch.utils.data import Dataset, DataLoader
import torchvision.models.video as models
import torchvision.models.detection as detection_models
import cv2
import os
import numpy as np
import pandas as pd
import glob
from tqdm import tqdm
from torch.cuda.amp import autocast, GradScaler
from sklearn.metrics import precision_recall_fscore_support, accuracy_score
from ultralytics import YOLO

# Hyperparameters
BATCH_SIZE = 8
EPOCHS = 2
LEARNING_RATE = 0.001
NUM_FRAMES = 16  # Number of frames per video clip
FRAME_SIZE = (112, 112)  # Resize frames

device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

# Dataset Class
class VideoDataset(Dataset):
    def __init__(self, video_paths, labels, transform=None):
        self.video_paths = video_paths
        self.labels = labels
        self.transform = transform

    def __len__(self):
        return len(self.video_paths)

    def __getitem__(self, idx):
        video_path = self.video_paths[idx]
        label = self.labels[idx]
        frames = self.load_video(video_path)
        if self.transform:
            frames = torch.stack([self.transform(frame) for frame in frames])
        return frames, torch.tensor(label, dtype=torch.long), video_path
    
    def load_video(self, path):
        cap = cv2.VideoCapture(path)
        frames = []
        total_frames = int(cap.get(cv2.CAP_PROP_FRAME_COUNT))
        if total_frames == 0:
            cap.release()
            return [torch.zeros((3, *FRAME_SIZE), dtype=torch.float32)] * NUM_FRAMES
        
        frame_indices = np.linspace(0, total_frames-1, NUM_FRAMES, dtype=int)
        
        for i in frame_indices:
            cap.set(cv2.CAP_PROP_POS_FRAMES, i)
            ret, frame = cap.read()
            if not ret:
                break
            frame = cv2.resize(frame, FRAME_SIZE)
            frame = cv2.cvtColor(frame, cv2.COLOR_BGR2RGB)
            frame = torch.tensor(frame, dtype=torch.float32).permute(2, 0, 1) / 255.0
            frames.append(frame)
        cap.release()
        
        if len(frames) == 0:
            return [torch.zeros((3, *FRAME_SIZE), dtype=torch.float32)] * NUM_FRAMES
        
        return frames if len(frames) == NUM_FRAMES else frames + [frames[-1]] * (NUM_FRAMES - len(frames))

# Load dataset dynamically
dataset_path = "Dataset"
brawl_videos = sorted(glob.glob(os.path.join(dataset_path, "Brawl", "Brawl_*.mp4")))
peace_videos = sorted(glob.glob(os.path.join(dataset_path, "Peace", "Peace_*.mp4")))

video_paths = brawl_videos + peace_videos
labels = [1] * len(brawl_videos) + [0] * len(peace_videos)

transform = transforms.Compose([transforms.Normalize((0.5,), (0.5,))])
dataset = VideoDataset(video_paths, labels, transform=transform)
dataloader = DataLoader(dataset, batch_size=BATCH_SIZE, shuffle=True, num_workers=0, pin_memory=True)

# Define Brawl Detection Model
class VideoClassifier(nn.Module):
    def __init__(self, num_classes=2):
        super(VideoClassifier, self).__init__()
        self.model = models.mc3_18(weights=models.MC3_18_Weights.DEFAULT)
        self.model.fc = nn.Linear(512, num_classes)
    
    def forward(self, x):
        return self.model(x)

# Define People Counting Model using YOLOv8
class PeopleCounter:
    def __init__(self):
        self.model = YOLO("yolov8n.pt")  # Load YOLOv8 pre-trained model

    def count_people_in_video(self, video_path):
        cap = cv2.VideoCapture(video_path)
        max_count = 0
        while cap.isOpened():
            ret, frame = cap.read()
            if not ret:
                break
            results = self.model(frame)
            count = sum(1 for det in results[0].boxes.cls if det == 0)  # Class 0 is 'person'
            max_count = max(max_count, count)
        cap.release()
        return max_count

people_counter = PeopleCounter()

# Training
model = VideoClassifier().to(device)
criterion = nn.CrossEntropyLoss()
optimizer = optim.Adam(model.parameters(), lr=LEARNING_RATE)
scaler = GradScaler()

def train():
    model.train()
    for epoch in range(EPOCHS):
        total_loss = 0
        for videos, labels, _ in tqdm(dataloader, desc=f"Epoch {epoch+1}/{EPOCHS}"):
            videos, labels = videos.to(device), labels.to(device)
            videos = videos.permute(0, 2, 1, 3, 4)
            optimizer.zero_grad()
            with autocast():
                outputs = model(videos)
                loss = criterion(outputs, labels)
            scaler.scale(loss).backward()
            scaler.step(optimizer)
            scaler.update()
            total_loss += loss.item()
        print(f"Epoch {epoch+1}/{EPOCHS}, Loss: {total_loss/len(dataloader):.4f}")
        
    # Save trained model
    torch.save(model.state_dict(), "brawl_detection_model.pth")
    print("Model saved successfully!")

if __name__ == "__main__":
    train()



C:\Users\ag168\AppData\Local\Temp\ipykernel_6068\1018633143.py:117: FutureWarning: `torch.cuda.amp.GradScaler(args...)` is deprecated. Please use `torch.amp.GradScaler('cuda', args...)` instead.
  scaler = GradScaler()
C:\Users\ag168\anaconda3\Lib\site-packages\torch\amp\grad_scaler.py:132: UserWarning: torch.cuda.amp.GradScaler is enabled, but CUDA is not available.  Disabling.
  warnings.warn(


'\nif __name__ == "__main__":\n    train()\n'

In [5]:
# Load trained model
model = VideoClassifier().to(device)
model.load_state_dict(torch.load("brawl_detection_model.pth", map_location=device))
model.eval()

people_counter = PeopleCounter()


test_dataset_path = "Test"
test_video_paths = sorted(glob.glob(os.path.join(test_dataset_path, "Video*.mp4")))
test_labels = [0] * len(test_video_paths)

test_dataset = VideoDataset(test_video_paths, test_labels, transform=transform)
test_dataloader = DataLoader(test_dataset, batch_size=BATCH_SIZE, shuffle=False, num_workers=0, pin_memory=True)

def predict_on_test_dataset():
    model.eval()
    predictions = []
    
    with torch.no_grad():
        for videos, _, paths in tqdm(test_dataloader, desc="Predicting"):
            videos = videos.to(device).permute(0, 2, 1, 3, 4)
            outputs = model(videos)
            preds = torch.argmax(outputs, dim=1).cpu().numpy()
            
            for path, pred in zip(paths, preds):
                person_count = people_counter.count_people_in_video(path) if pred == 1 else 0
                predictions.append((os.path.basename(path), int(pred), person_count))

    df = pd.DataFrame(predictions, columns=["videoID", "predicted_label", "person_count"])
    return df

test_results = predict_on_test_dataset()

Predicting:   0%|                                                                               | 0/50 [00:00<?, ?it/s]


0: 640x640 2 persons, 1 skateboard, 161.0ms
Speed: 8.0ms preprocess, 161.0ms inference, 1.7ms postprocess per image at shape (1, 3, 640, 640)

0: 640x640 2 persons, 1 skateboard, 158.7ms
Speed: 6.3ms preprocess, 158.7ms inference, 1.6ms postprocess per image at shape (1, 3, 640, 640)

0: 640x640 2 persons, 1 skateboard, 144.8ms
Speed: 6.7ms preprocess, 144.8ms inference, 1.7ms postprocess per image at shape (1, 3, 640, 640)

0: 640x640 3 persons, 1 skateboard, 157.9ms
Speed: 7.9ms preprocess, 157.9ms inference, 1.4ms postprocess per image at shape (1, 3, 640, 640)

0: 640x640 2 persons, 143.6ms
Speed: 6.8ms preprocess, 143.6ms inference, 1.6ms postprocess per image at shape (1, 3, 640, 640)

0: 640x640 2 persons, 140.9ms
Speed: 6.7ms preprocess, 140.9ms inference, 1.3ms postprocess per image at shape (1, 3, 640, 640)

0: 640x640 1 person, 154.7ms
Speed: 6.8ms preprocess, 154.7ms inference, 1.3ms postprocess per image at shape (1, 3, 640, 640)

0: 640x640 1 person, 1 skateboard, 1 bott

Predicting:   2%|█▎                                                                  | 1/50 [01:50<1:29:57, 110.16s/it]


0: 640x512 1 person, 139.5ms
Speed: 5.4ms preprocess, 139.5ms inference, 1.2ms postprocess per image at shape (1, 3, 640, 512)

0: 640x512 1 person, 117.6ms
Speed: 5.0ms preprocess, 117.6ms inference, 1.3ms postprocess per image at shape (1, 3, 640, 512)

0: 640x512 2 persons, 1 umbrella, 113.0ms
Speed: 3.5ms preprocess, 113.0ms inference, 1.3ms postprocess per image at shape (1, 3, 640, 512)

0: 640x512 1 person, 113.3ms
Speed: 3.6ms preprocess, 113.3ms inference, 1.2ms postprocess per image at shape (1, 3, 640, 512)

0: 640x512 1 person, 112.7ms
Speed: 3.3ms preprocess, 112.7ms inference, 1.4ms postprocess per image at shape (1, 3, 640, 512)

0: 640x512 1 person, 121.2ms
Speed: 4.2ms preprocess, 121.2ms inference, 1.3ms postprocess per image at shape (1, 3, 640, 512)

0: 640x512 1 person, 114.4ms
Speed: 3.4ms preprocess, 114.4ms inference, 1.3ms postprocess per image at shape (1, 3, 640, 512)

0: 640x512 1 person, 110.7ms
Speed: 3.7ms preprocess, 110.7ms inference, 1.4ms postprocess

Predicting:   4%|██▋                                                                 | 2/50 [03:30<1:23:22, 104.22s/it]

...

Predicting:  96%|█████████████████████████████████████████████████████████████████▎  | 48/50 [1:18:34<02:37, 78.58s/it]


0: 608x640 2 persons, 121.1ms
Speed: 5.9ms preprocess, 121.1ms inference, 1.6ms postprocess per image at shape (1, 3, 608, 640)

0: 608x640 1 person, 164.1ms
Speed: 6.7ms preprocess, 164.1ms inference, 1.4ms postprocess per image at shape (1, 3, 608, 640)

0: 608x640 3 persons, 1 mouse, 135.5ms
Speed: 6.7ms preprocess, 135.5ms inference, 1.3ms postprocess per image at shape (1, 3, 608, 640)

0: 608x640 1 person, 145.0ms
Speed: 6.9ms preprocess, 145.0ms inference, 1.3ms postprocess per image at shape (1, 3, 608, 640)

0: 608x640 1 person, 117.9ms
Speed: 6.5ms preprocess, 117.9ms inference, 1.5ms postprocess per image at shape (1, 3, 608, 640)

0: 608x640 2 persons, 115.5ms
Speed: 5.7ms preprocess, 115.5ms inference, 1.5ms postprocess per image at shape (1, 3, 608, 640)

0: 608x640 2 persons, 116.5ms
Speed: 5.9ms preprocess, 116.5ms inference, 1.9ms postprocess per image at shape (1, 3, 608, 640)

0: 608x640 2 persons, 113.4ms
Speed: 5.6ms preprocess, 113.4ms inference, 1.4ms postproces

Predicting:  98%|██████████████████████████████████████████████████████████████████▋ | 49/50 [1:20:14<01:25, 85.01s/it]


0: 640x640 2 persons, 2 umbrellas, 1 tv, 1 laptop, 117.8ms
Speed: 4.7ms preprocess, 117.8ms inference, 1.2ms postprocess per image at shape (1, 3, 640, 640)

0: 640x640 2 persons, 1 tv, 2 laptops, 113.4ms
Speed: 4.9ms preprocess, 113.4ms inference, 1.2ms postprocess per image at shape (1, 3, 640, 640)

0: 640x640 3 persons, 1 laptop, 115.8ms
Speed: 5.5ms preprocess, 115.8ms inference, 1.3ms postprocess per image at shape (1, 3, 640, 640)

0: 640x640 2 persons, 1 laptop, 116.8ms
Speed: 5.7ms preprocess, 116.8ms inference, 1.1ms postprocess per image at shape (1, 3, 640, 640)

0: 640x640 3 persons, 1 laptop, 116.7ms
Speed: 5.1ms preprocess, 116.7ms inference, 1.1ms postprocess per image at shape (1, 3, 640, 640)

0: 640x640 2 persons, 1 laptop, 118.5ms
Speed: 4.9ms preprocess, 118.5ms inference, 1.1ms postprocess per image at shape (1, 3, 640, 640)

0: 640x640 2 persons, 1 laptop, 116.6ms
Speed: 5.0ms preprocess, 116.6ms inference, 1.6ms postprocess per image at shape (1, 3, 640, 640)



Predicting: 100%|████████████████████████████████████████████████████████████████████| 50/50 [1:21:22<00:00, 97.65s/it]


In [8]:
test_results.to_csv('Prediction_result_final.csv',index=False)